In [27]:
#import urllib2
from io import StringIO
import os
import sys
import glob

import requests
import xmltodict

import pandas as pd
from datetime import datetime 
import statsmodels.api as sm
from statsmodels.sandbox.regression.predstd import wls_prediction_std

import geopandas as gpd

import numpy as np

import pymannkendall as mk

import matplotlib
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib as mpl

import platform
import geopandas

import folium

from pylab import rcParams
%matplotlib inline
matplotlib.rc_file_defaults()
rcParams['figure.figsize'] = 15, 10

In [2]:
print("Operating System " + platform.system() + " " + platform.release())
print("Python Version " + str(sys.version))
print("Pandas Version " + str(pd.__version__))
print("Numpy Version " + str(np.__version__))
print("Matplotlib Version " + str(mpl.__version__))
#print("Well Application Version " + str(wa.__version__))
print("Scipy Version " +str(scipy.__version__))
print (os.environ['CONDA_DEFAULT_ENV'])

Operating System Windows 10
Python Version 3.9.4 | packaged by conda-forge | (default, May 10 2021, 22:10:34) [MSC v.1916 64 bit (AMD64)]
Pandas Version 1.2.4
Numpy Version 1.20.2
Matplotlib Version 3.4.2
Scipy Version 1.6.3
pygis39


Webservices now available at https://streamstats.usgs.gov/docs/streamstatsservices/ but they are still in developement.

Data downloaded from manually processing on https://streamstats.usgs.gov/ss/

# Import Pour Point Data

Import the stream points.  This file was created by hand in ArcGIS using a topographic base and air photos.  Each tributary and major points of interest were selected. Points were created on the streams designated on the topo.  Some points may not clip exactly to the STREAMSTATS stream line and may have to be adjusted.

In [29]:
stream_points = gpd.read_file("G:/Shared drives/UGS_Groundwater/Projects/Bryce/GIS/NHDStreamsHighREs.gdb", driver='FileGDB', layer="streamstats_points")

In [30]:
stream_points

name   latitude   longitude  \
0                      End  38.010925 -111.965783   
1               Deer Creek  38.011222 -111.966045   
2                Cow Creek  37.996110 -111.973843   
3         Cottonwood Creek  37.955136 -111.980223   
4               Rock Creek  37.907604 -112.018529   
5           Prospect Creek  37.884203 -112.023285   
6         Sweetwater Creek  37.882742 -112.020251   
7              South Creek  37.857212 -112.029841   
8               Clay Creek  37.851088 -112.033775   
9                East Fork  37.815080 -112.107826   
10               West Fork  37.810929 -112.108243   
11         Pat Willis Draw  37.729230 -112.134777   
12             Swale Creek  37.726425 -112.149691   
13        Mud Spring Creek  37.703441 -112.196168   
14     Coyote Hollow Creek  37.696605 -112.202429   
15            Badger Creek  37.592925 -112.259222   
16              Tropic Out  37.613983 -112.249942   
17               Tropic In  37.575887 -112.266184   
18  Tropic Ditch Diversion  37.650699 -112.225754   
19   East Creek Nat Forest  37.644024 -112.226006   
20           Dave's Hollow  37.674845 -112.206075   
21         Ahlstrom Hollow  37.672680 -112.222534   
22                Blue Fly  37.644885 -112.233915   
23           Blubber Creek  37.547561 -112.279475   
24             Kanab Creek  37.533547 -112.286585   
25            Podunk Creek  37.495466 -112.291615   
26         Upper East Fork  37.493715 -112.293546   
27             Ranch Creek  37.902569 -111.978463   
28             Birch Creek  37.883595 -111.970648   
29             Horse Creek  37.874220 -111.965271   
30        Upper Clay Creek  37.790484 -112.000432   
31            Cameron Wash  37.773105 -112.032906   

                                  huc12  \
0                          160300020407   
1                          160300020408   
2                          160300020407   
3                          160300020406   
4                          160300020404   
5                          160300020404   
6                          160300020403   
7                          160300020402   
8                          160300020402   
9                          160300020306   
10                         160300020306   
11                         160300020304   
12                         160300020304   
13                         160300020303   
14                         160300020303   
15                         160300020302   
16                         160300020303   
17                         160300020302   
18                         160300020303   
19                         160300020303   
20                         160300020303   
21                         160300020303   
22                         160300020303   
23                         160300020302   
24                         160300020301   
25                         160300020301   
26                         160300020301   
27             Ranch Creek-Sevier River   
28             Ranch Creek-Sevier River   
29                     Sweetwater Creek   
30                           Clay Creek   
31  Cameron Wash-East Fork Sevier River   

                                    hucname                     geometry  
0                    Cow Creek-Sevier River  POINT (-111.96578 38.01092)  
1                                Deer Creek  POINT (-111.96604 38.01122)  
2                    Cow Creek-Sevier River  POINT (-111.97384 37.99611)  
3                          Cottonwood Creek  POINT (-111.98022 37.95514)  
4                            Prospect Creek  POINT (-112.01853 37.90760)  
5                            Prospect Creek  POINT (-112.02329 37.88420)  
6                          Sweetwater Creek  POINT (-112.02025 37.88274)  
7                               South Creek  POINT (-112.02984 37.85721)  
8                               South Creek  POINT (-112.03377 37.85109)  
9                                Hunt Creek  POINT (-112.10783 37.81508)  
10                         

# Create STREAMSTATS Workspaces

STREAMSTATS uses cloud computing workspaces to designate an area being calculated.  To generate a workspace, we have to give STREAMSTATS pour point coordinates.  STREAMSTATS will delineate a watershed representing upstream contributions of this point.

In [47]:

def get_workspace(df):
    """
    This function uses the USGS STREAMSTATS api to create a workspace for each point in the streamstats points file.
    STREAMSTATS will delineate the upstream area of a given point, assuming that point is on a stream.
    """
    parms = {}
    url = "https://streamstats.usgs.gov/streamstatsservices/watershed.geojson?"
    parms['rcode'] = 'UT'
    parms['xlocation'] = df['longitude']
    parms['ylocation'] = df['latitude']
    parms['crs'] = 4326 
    parms['includeparameters'] = 'false'
    parms['includeflowtypes'] = 'false'
    parms['includefeatures'] = 'true'
    parms['simplify'] = 'true'
    response_ob = requests.get(url, params=parms)
    
    try:
        resp_json = response_ob.json()
        wrkspc = resp_json['workspaceID']
        ss_pnt = resp_json['featurecollection'][0]['feature']
        ss_poly = resp_json['featurecollection'][1]['feature']
        df['workspace'] = wrkspc
        df['ss_poly'] = ss_poly
        df['ss_point'] = ss_pnt
    except Exception as e: 
        print(e)
        print(f"{df['name']} failed.")
        pass
    return df

Note that running the function will take a while.

In [48]:
stream_points = stream_points.apply(lambda x: get_workspace(x),1)

In [159]:
stream_points.head()

name   latitude   longitude         huc12  \
0               End  38.010925 -111.965783  160300020407   
1        Deer Creek  38.011222 -111.966045  160300020408   
2         Cow Creek  37.996110 -111.973843  160300020407   
3  Cottonwood Creek  37.955136 -111.980223  160300020406   
4        Rock Creek  37.907604 -112.018529  160300020404   

                  hucname               workspace  \
0  Cow Creek-Sevier River  UT20210729151927014000   
1              Deer Creek  UT20210729151948047000   
2  Cow Creek-Sevier River  UT20210729152009449000   
3        Cottonwood Creek  UT20210729152030444000   
4          Prospect Creek  UT20210729152051484000   

                                             ss_poly  \
0  {'type': 'FeatureCollection', 'crs': {'type': ...   
1  {'type': 'FeatureCollection', 'crs': {'type': ...   
2  {'type': 'FeatureCollection', 'crs': {'type': ...   
3  {'type': 'FeatureCollection', 'crs': {'type': ...   
4  {'type': 'FeatureCollection', 'crs': {'type': ...   

                      geometry  
0  POINT (-111.96578 38.01092)  
1  POINT (-111.96604 38.01122)  
2  POINT (-111.97384 37.99611)  
3  POINT (-111.98022 37.95514)  
4  POINT (-112.01853 37.90760)

## Save GIS Output

In [81]:
stream_points.to_file("G:/Shared drives/UGS_Groundwater/Projects/Bryce/GIS/streamstatspointsout.geojson",driver='GeoJSON')

# Plot Workspaces

In [82]:
stream_points = gpd.read_file("G:/Shared drives/UGS_Groundwater/Projects/Bryce/GIS/streamstatspointsout.geojson",driver='GeoJSON')

In [83]:
# https://nbviewer.jupyter.org/github/python-visualization/folium/blob/master/examples/GeoJSON_and_choropleth.ipynb

mapViz = folium.Map(location=[ stream_points['latitude'].mean(),stream_points['longitude'].mean()],
                    tiles='Stamen Terrain', 
                    zoom_start=10)

#folium.LayerControl().add_to(m)
mpitm = {}

#folium.LayerControl().add_to(m)
mpitm = {}
for name in stream_points['name'].unique():
    gdf = stream_points[stream_points['name']==name]
    mpitm[name+"pnt"] = folium.GeoJson(data=gdf['ss_poly'].values[0]).add_to(mapViz)
    mpitm[name] = folium.GeoJson(data=gdf['ss_poly'].values[0]).add_to(mapViz)    
    mpitm[name].add_child(folium.Popup(f"{gdf['name'].values[0]:} "))
    mpitm[name+"pnt"].add_child(folium.Popup(f"{gdf['name'].values[0]:} "))
    
mapViz

folium.GeoJson(data=response_ob.json()['featurecollection'][1]['feature']).add_to(mapViz)    
#mp.add_child(folium.Popup(f"{gdf['Name'].values[0]:}\n{gdf['HUC12'].values[0]:}\n{gdf['AreaAcres'].values[0]:0.0f}acres"))
    
    
mapViz

# Get Flow Statistics

In [125]:
def get_flows(workspace):
    """
    This function uses the USGS STREAMSTATS api to estimate flow statistics based on pre-designated workspaces
    """
    parms = {}
    url = "https://streamstats.usgs.gov/streamstatsservices/flowstatistics.json?"
    parms['rcode'] = 'UT'
    parms['workspaceID'] = workspace
    parms['includeflowtypes'] = 'true'
    response_ob = requests.get(url, params=parms)
    
    resp_json = response_ob.json()
    return resp_json

def assemble_flow(workspace):
    """
    This function takes the json file that the api spits out and chops out the useful information.  
    json is kinda like a series of nested dictionaries and lists.
    """
    # contact api and ask for flow information by workspaceid
    test_flows = get_flows(workspace)
    
    # get annual flow and annual flow error from output
    ann_flow = test_flows[1]['RegressionRegions'][0]['Results'][0]['Value']
    ann_flow_err = test_flows[1]['RegressionRegions'][0]['Results'][0]['Errors'][0]['Value']

    mo_flow = {}

    mo_flow['workspace'] = workspace
    mo_flow['annual'] = ann_flow
    mo_flow['annual error'] = ann_flow_err
    # extract nested monthly data and put it into a new dictionary
    for mo in range(2,14):
        mo_flow[f"{mo-1}_80"] = test_flows[mo]['RegressionRegions'][0]['Results'][0]['Value']
        mo_flow[f"{mo-1}_80_err"] = test_flows[mo]['RegressionRegions'][0]['Results'][0]['Errors'][0]['Value']
        mo_flow[f"{mo-1}_50"] = test_flows[mo]['RegressionRegions'][0]['Results'][1]['Value']
        mo_flow[f"{mo-1}_50_err"] = test_flows[mo]['RegressionRegions'][0]['Results'][1]['Errors'][0]['Value']
        mo_flow[f"{mo-1}_20"] = test_flows[mo]['RegressionRegions'][0]['Results'][1]['Value']
        mo_flow[f"{mo-1}_20_err"] = test_flows[mo]['RegressionRegions'][0]['Results'][1]['Errors'][0]['Value']
    
    # convert the dictionary into a Pandas Series
    ser = pd.Series(mo_flow)
    return ser
    

This iterator goes through each workspace and tries to pull flow data.  
Sometimes api connections are spotty, so it will try to pull the data four times before giving up and moving on.
It looks like some of the points don't work, so we will have to figure that out.

In [126]:
# this iterator goes through each workspace and tries to pull flow data.  
# Sometimes api connections are spotty, so it will try to pull the data four times before giving up and moving on.
flws = {}

for wrkspc in stream_points['workspace'].unique():
    if wrkspc not in flws.keys():
        print(wrkspc)
        i = 0
        while i < 4:
            try:
                flws[wrkspc] = assemble_flow(wrkspc)
                i = 4
            except:
                i+=1
                print(f"{wrkspc} failed try {i}")


UT20210729151927014000
UT20210729151927014000 failed try 1
UT20210729151948047000
UT20210729151948047000 failed try 1
UT20210729152009449000
UT20210729152030444000
UT20210729152051484000
UT20210729152112326000
UT20210729152133836000
UT20210729152156743000
UT20210729152156743000 failed try 1
UT20210729152156743000 failed try 2
UT20210729152156743000 failed try 3
UT20210729152156743000 failed try 4
UT20210729152218831000
UT20210729152218831000 failed try 1
UT20210729152218831000 failed try 2
UT20210729152218831000 failed try 3
UT20210729152218831000 failed try 4
UT20210729152240255000
UT20210729152240255000 failed try 1
UT20210729152240255000 failed try 2
UT20210729152240255000 failed try 3
UT20210729152240255000 failed try 4
UT20210729152403713000
UT20210729152403713000 failed try 1
UT20210729152425994000
UT20210729152425994000 failed try 1
UT20210729152448546000
UT20210729152448546000 failed try 1
UT20210729152448546000 failed try 2
UT20210729152448546000 failed try 3
UT202107291524485

In [ ]:
# Combine the resulting flow data into one DataFrame

In [127]:
flows = pd.concat(flws,axis=1)

In [128]:
def parseind(x):
    ind = x.name
    if "_" in ind:
        indlist = ind.split("_")
        x['month'] = indlist[0]
        x['percent'] = indlist[1]
        if len(indlist) == 3 and indlist[2] =='err':
            x['report'] = 'error'
        else:
            x['report'] = 'value'
    else:
        x['report'] = ind
        pass
    return x
flows = flows.apply(lambda x: parseind(x),1)
flows = flows.drop(index=['workspace'],axis=0)

In [131]:
sorted_flows = flows.set_index(['month','percent','report'])
sorted_flows = sorted_flows.reset_index()

Rename columns to more reasonable names

In [135]:
sorted_flows = sorted_flows.rename(columns=stream_points.set_index('workspace')['name'].to_dict())

# Get Basin Characteristics

In [149]:
def get_chars(workspace):
    """
    This function uses the USGS STREAMSTATS api to download the basin characteristics based on pre-designated workspaces
    """
    parms = {}
    url = "https://streamstats.usgs.gov/streamstatsservices/parameters.json?"
    parms['rcode'] = 'UT'
    parms['workspaceID'] = workspace
    parms['includeparameters'] = 'true'
    print(workspace)
    i = 0
    df = []
    while i < 4:
        try:
            response_ob = requests.get(url, params=parms)
            resp_json = response_ob.json()['parameters']
            df = pd.DataFrame.from_dict(resp_json)
            i = 4
            
        except:
            i+=1
            print(f"{workspace} failed try {i}")
            
            pass
    return df

In [152]:
basin_char = {}
for wrkspc in stream_points['workspace'].unique():
    df = get_chars(wrkspc)
    if len(df) > 0:
        basin_char[wrkspc] = df

UT20210729151927014000
UT20210729151948047000
UT20210729151948047000 failed try 1
UT20210729151948047000 failed try 2
UT20210729151948047000 failed try 3
UT20210729151948047000 failed try 4
UT20210729152009449000
UT20210729152030444000
UT20210729152030444000 failed try 1
UT20210729152030444000 failed try 2
UT20210729152030444000 failed try 3
UT20210729152030444000 failed try 4
UT20210729152051484000
UT20210729152112326000
UT20210729152112326000 failed try 1
UT20210729152112326000 failed try 2
UT20210729152112326000 failed try 3
UT20210729152112326000 failed try 4
UT20210729152133836000
UT20210729152156743000
UT20210729152218831000
UT20210729152240255000
UT20210729152403713000
UT20210729152425994000
UT20210729152425994000 failed try 1
UT20210729152425994000 failed try 2
UT20210729152425994000 failed try 3
UT20210729152425994000 failed try 4
UT20210729152448546000
UT20210729152448546000 failed try 1
UT20210729152448546000 failed try 2
UT20210729152448546000 failed try 3
UT202107291524485

In [157]:
basin_characters = pd.concat(basin_char)
basin_characters = basin_characters.rename(index=stream_points.set_index('workspace')['name'].to_dict())
basin_characters.head()

ID                           name  \
End 0   0       Mean April Precipitation   
    1   0      Mean August Precipitation   
    2   0  Mean Basin Slope from 10m DEM   
    3   0    Mean December Precipitation   
    4   0                  Drainage Area   

                                   description       code          unit  \
End 0                 Mean April Precipitation   APRAVPRE        inches   
    1                Mean August Precipitation   AUGAVPRE        inches   
    2  Mean basin slope computed from 10 m DEM  BSLDEM10M       percent   
    3              Mean December Precipitation   DECAVPRE        inches   
    4  Area that drains to a point on a stream    DRNAREA  square miles   

        value  
End 0    1.24  
    1    2.09  
    2   17.60  
    3    1.24  
    4  493.00

# Export Results

In [158]:
with pd.ExcelWriter('G:/Shared drives/UGS_Groundwater/Projects/Bryce/GIS/STREAMSTATS_output.xlsx') as writer:  
    sorted_flows.to_excel(writer, sheet_name='flow_stats')
    stream_points.to_excel(writer, sheet_name='delineation_points')
    basin_characters.to_excel(writer, sheet_name='basin_characteristics')